# Cross Correlation Matrix

In [59]:
import xarray as xr
import ODLintake
import pandas as pd
import numpy as np
from geopy import distance
import hvplot.pandas  # noqa
import hvplot.xarray
import holoviews as hv
from holoviews import dim, opts
from tqdm import tqdm
from dask.distributed import Client
from matplotlib import pyplot as plt
from scipy import signal
from numpy import matlib
from NI_tools.NI_tools import calculate
from xrsignal import xrsignal
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [2]:
client = Client()
client

<Client: 'tcp://127.0.0.1:42759' processes=8 threads=32, memory=62.80 GiB>

## Get Things Set Up

### Look at PSD

In [18]:
fn = '/datadrive/DAS/psd_distance.nc'
psd = xr.open_dataarray(fn)
psd = psd.rename({'distance':'index'})

In [23]:
psd_plot = (10*np.log10(psd)).hvplot.image(x='index', y='time_frequency', rasterize=True, width=1000, height=500)
depth_plot = geo.hvplot.scatter(x='index', y='depth', height=200, width=1000, grid=True)

In [24]:
(psd_plot + depth_plot).cols(1)

:Layout
   .DynamicMap.I :DynamicMap   []
      :Image   [index,time_frequency]   (psd across time dimension)
   .Scatter.I    :Scatter   [index]   (depth)

### Let's operate under the assumption that the left column is idx

In [32]:
idx = 1001
point1 = (geo.loc[idx].lat, geo.loc[idx].lon)
point2 = (geo.loc[idx+1].lat, geo.loc[idx+1].lon)
print(distance.distance(point1, point2).meters)

1.707154417177408


In [5]:
geo = pd.read_csv('south_DAS_latlondepth.txt')

In [51]:
geo

index        lat        lon        depth
0        942.0  45.202300 -123.96715     7.066498
1        943.0  45.202294 -123.96717     6.966902
2        944.0  45.202289 -123.96720     6.809939
3        945.0  45.202283 -123.96722     6.693391
4        946.0  45.202278 -123.96725     6.515923
...        ...        ...        ...          ...
46435  47377.0  45.148720 -125.11567 -1574.027300
46436  47378.0  45.148718 -125.11569 -1574.032300
46437  47379.0  45.148717 -125.11572 -1574.037500
46438  47380.0  45.148715 -125.11574 -1574.044200
46439  47381.0  45.148713 -125.11577 -1574.053500

[46440 rows x 4 columns]

In [17]:
plot = hv.Scatter3D((geo.lon, geo.lat, geo.depth)).opts(width=1000, height=500, color='#000000', size=1)
plot

:Scatter3D   [x,y,z]

### Load small slice to datadrive

In [5]:
ds = ODLintake.open_ooi_DAS_SouthTx()
ds = ds.isel({'distance':slice(942,47382)})

In [6]:
da = ds.isel({'distance':slice(8000, 8100)})['RawData']

In [8]:
da.to_netcdf('/datadrive/DAS/slices/8000_81000_slice.nc')

## Build Pre-processing function

- with whatever brute force methods are necesary

In [3]:
fn = '/datadrive/DAS/slices/8000_81000_slice.nc'
da = xr.open_dataarray(fn)
da = da.chunk({'distance':100, 'time':200*120})

In [4]:
b,a = signal.butter(4, [0.01, 0.9], btype='bandpass')

In [5]:
da_pp = calculate.preprocess(da, dim='time')

## Compute MultiElement NCCF

In [48]:
NCCF_me = calculate.compute_MultiElement_NCCF(da_pp).mean('time')

In [50]:
NCCF_me_data = NCCF_me.compute()

In [65]:
NCCF_me_data.hvplot.image(rasterize=True)

:DynamicMap   []
   :Image   [delay,distance]   (multi-element NCCF)

In [61]:
NCCF_me_c = xrsignal.hilbert_mag(NCCF_me_data, dim='delay')

In [66]:
(20*np.log10(NCCF_me_c)).hvplot.image(rasterize=True)

:DynamicMap   []
   :Image   [delay,distance]   (value)